# Box Office Revenue Prediction

## Imports

In [392]:
import pandas as pd
import numpy as np


import re # regex
import ast

from datetime import datetime
from datetime import date

from sklearn import preprocessing
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import MultinomialNB
from sklearn.neighbors import KNeighborsClassifier
from sklearn.pipeline import make_pipeline
from sklearn.model_selection import cross_val_score, learning_curve, GridSearchCV, RandomizedSearchCV, train_test_split

## Data Sources
1. IMDB:
    * No. of ratings (star)
    * Avg. star rating (out of 10)
    * No. of user ratings (text reviews)
    * No. of critic ratings (meta critic)
    * Countries (truncate to just first country) - √
    * Language (truncate to just first language) - √
    * No. of languages (to be created from previous column) - √
    * Production house (truncate to just first production house) - √
    * Duration (convert to minutes/numeric from string) - √
    * Genre (need to explode to one-hot columns for 24 genres) - √
    * MPAA rating 
        * TV- ratings - reclassify - √ 
        * **`TODO`** Not Rated/Unrated - many from non-English fall under these categories
    * **Gross:** 'Y' variable (need to remove movies with alphabet-only gross, convert INR (other currencies?) to USD and 3 INR 3-digit movies)
        * **`TODO`** Convert currency using exchange rate from date of release, instead of current exchange rates
     
    * **`TODO`** Release date + release region - separate out into 2 columns, convert first to datetime and use as a feature (weekend release/not)
    
&nbsp; 
2. Popularity Scores:
    * Average popularity score per movie

&nbsp; 

3. Sentiment Scores (**`TODO`**):
    * Positive score - based on IMDB user reviews
    * Negative score - based on IMDB user reviews
    

&nbsp;    
4. YouTube (**`TODO`**):
    * View count
    * Like count
    * Dislike count
    * Comment count

## Reading Excel File(s)

In [298]:
# read xlsx with IMDB_ID as the indexing column (2nd column from the left, or 1st column)
df = pd.read_excel("Final_data_sheets_updated_popularity_scores.xlsx", index_col = 1)

In [ ]:
# inspect
df.head(10)

In [ ]:
df.shape

In [299]:
df = df.drop(['Unnamed: 0', 'main_cast_list', 'main_cast_links','dir_list','creator_list', 'meta_critic_score','story_line', 'others'], axis = 1)

In [ ]:
df.head(3)

In [ ]:
df.shape

## Data Transformations

### 1. Check for NAs/NANs

In [ ]:
df.describe()

In [ ]:
df.shape

#### Columns with NAs
MPAA rating, num_user_ratings, num_critic_ratings, language, production_house

In [ ]:
df.isnull().any()

#### How many NAs total?
Could be multiple NAs for a given row.

In [ ]:
df.isnull().sum().sum()

#### How many NAs per column?
Can it be manually fixed by finding the true value? Say, for duration of a couple of movies.

In [ ]:
df.isnull().sum(axis = 0)

In [ ]:
df[df['duration'].isnull()]

This anyway has other columns as NaNs (info isn't available on IMDB anymore?),  so might as well drop the row.

#### If dropping all NAs?

In [300]:
# Lose 487 rows
df = df.dropna()
df.shape

(3867, 14)

### 2. Add number of languages

In [ ]:
# inspect unique values
df.Language.unique()

In [301]:
languages_split = df.Language.str.split(pat="|")
df['num_languages'] = languages_split.str.len()

In [ ]:
# inspect
df.head(3)

In [ ]:
# check NaN
df['num_languages'].isnull().values.any()

### 3. Truncate 'Languages' and 'Country'

In [ ]:
# inspect unique values
df.Country.unique()

In [302]:

languages_split = df.Language.str.split(pat="|").apply(lambda x: x[0])
df['Language'] = languages_split

In [303]:
countries_split = df.Country.str.split(pat="|").apply(lambda x: x[0])
df['Country'] = countries_split

In [ ]:
df.head(3)

In [ ]:
# check both columns for NaN
print(df['Language'].isnull().values.any())
print(df['Country'].isnull().values.any())

In [233]:
# check how many unique values of each
print(len(df.Country.unique()))
print(len(df.Language.unique()))

77
61


### 4. Truncate 'Production_House'

In [ ]:
# inspect unique values - 3697 of them, can't see all
df.Production_House.unique()

In [304]:
production_house_split = df.Production_House.str.split(pat=", ").apply(lambda x: x[0])
df['Production_House'] = production_house_split

In [ ]:
# still could too unqiue of a column - 2277 unique values!
len(df.Production_House.unique())

### 5. Check MPAA column and regroup
https://simple.m.wikipedia.org/wiki/Motion_Picture_Association_of_America_film_rating_system

#### **Reclassification:**
* TV-Y, TV-7, TV-G --> G
* TV-PG --> PG
* TV-14 --> PG-13
* TV-MA --> R
* Not Rated (923!) --> 
* Unrated (143) -->

In [ ]:
# check NaN
df['motion_picture_rating'].isnull().values.any()

In [ ]:
# what are the unique ratings, and how many in each category?
df.groupby('motion_picture_rating').size()

In [307]:
df.loc[df['motion_picture_rating'].isin(["TV-G", "TV-Y7", "TV-Y"]), 'motion_picture_rating'] = "G"
df.loc[df['motion_picture_rating'].isin(["TV-PG"]), 'motion_picture_rating'] = "PG"
df.loc[df['motion_picture_rating'].isin(["TV-14"]), 'motion_picture_rating'] = "PG-13"
df.loc[df['motion_picture_rating'].isin(["TV-MA"]), 'motion_picture_rating'] = "R"

# df.loc[df['motion_picture_rating'].isin(["Unrated"]), 'motion_picture_rating'] = " "
# df.loc[df['motion_picture_rating'].isin(["Not Rated"]), 'motion_picture_rating'] = " "

df.groupby('motion_picture_rating').size()

motion_picture_rating
G              45
NC-17           2
Not Rated     923
PG            369
PG-13         937
R            1448
Unrated       143
dtype: int64

In [ ]:
df[df['motion_picture_rating'] == "Not Rated"].head(5)

In [ ]:
df[df['motion_picture_rating'] == "Unrated"].head(5)

In [ ]:
# check NaN after transforming
df['motion_picture_rating'].isnull().values.any()

### 6. Convert 'duration' column to time in minutes (integer)

In [308]:
def check_time(time):
    if len(time) == 1:
        if "h" in time[0]:
            new_time = 60*int(re.sub("\D", "", time[0]))
        else:
            new_time = int(re.sub("\D", "", time[0]))
    else:
        new_time = 60*int(re.sub("\D", "", time[0])) + int(re.sub("\D", "", time[1]))
    return new_time

test1 = df.duration.str.split(" ")
test2 = test1.apply(lambda x: check_time(x))

df['duration'] = test2

In [84]:
# check unique values
print(df.duration.unique())

[ 98 100 118 106  91 117 125 103 138 107 128  94 101 108 165 115  92 132
 104 113  93 110 111  88  97  87 124  90  95 105 140 112 116 146 109  81
  84 148 102 114  80  99 163  79 135  82  96 120 133  44 123  86 122 129
 130 334  85 121 134 142 119  89  83 139 141 131 136 154  63  75 180 272
 157 155 143 127 150 137 126 164 158  76 145  70  78 144 147 172 169 151
  40 152  77 149 186  59 153 161 160 220  71 167  74 188 201 183 226 166
  68  69 185 168 159 173 162  60 156 270 187  72  39 176  73 174 171 190
 170  46  66]


In [ ]:
## check for NaNs after transforming
df['duration'].isnull().values.any()

### 7. Expanding 'genre' to one-hot columns

In [ ]:
type(df['genre'].iloc[0]) # Need to convert string representation of list to an actual Python list to accumulate as et later

In [ ]:
# check unique genre lists
unique_genre_lists = df['genre'].unique()
print(unique_genre_lists) 

In [309]:
def convert_to_list(x):
    if "[" in x:
        x = re.sub("[\[\]]", "", x)
        x = x.split(", ")
    else:
        x = x.split(" ") # split by non-existent delimiter
    return x

In [310]:
# get all unique genres available
genre_lists = df.genre.apply(lambda x: convert_to_list(x))
df.genre = genre_lists

# temp = genre_lists.tolist()
# flattened =  [y for x in temp for y in x]
# print(set(flattened))

In [116]:
type(df['genre'].iloc[0])

list

In [311]:
# add 23 new one-hot columns
from sklearn.preprocessing import MultiLabelBinarizer

mlb = MultiLabelBinarizer()
df = df.join(pd.DataFrame(mlb.fit_transform(df.pop('genre')),
                          columns=mlb.classes_,
                          index=df.index))

In [272]:
df.head(3)

Name  num_ratings  avg_rating motion_picture_rating  \
IMDB_ID                                                                   
433362       Daybreakers       116014         6.5                     R   
1216492        Leap Year        85208         6.5                    PG   
1037705  The Book of Eli       268523         6.9                     R   

                         release_date  duration  num_user_ratings  \
IMDB_ID                                                             
433362    14 January 2010 (Singapore)        98             301.0   
1216492  12 February 2010 (Singapore)       100             219.0   
1037705     18 March 2010 (Singapore)       118             588.0   

         num_critic_ratings          Gross    Country  ... Musical Mystery  \
IMDB_ID                                                ...                   
433362                291.0     51,416,464  Australia  ...       0       0   
1216492               136.0    25,918,920         USA  ...       0       0   
1037705               331.0   157,107,755         USA  ...       0       0   

         News  Romance  Sci-Fi  Short  Sport  Thriller  War  Western  
IMDB_ID                                                               
433362      0        0       1      0      0         1    0        0  
1216492     0        1       0      0      0         0    0        0  
1037705     0        0       0      0      0         1    0        0  

[3 rows x 37 columns]

In [273]:
# check for NaNs after transforming in all genre columns
df.shape

(3867, 37)

### 8. Release date to datetime and release location as a separate column

### 9. Cleaning up 'Gross'
Standardize currency, hard-code 3-digit movies, convert string to int/float

In [ ]:
type(df['Gross'].iloc[0])

In [312]:
pd.set_option('display.max_row', 4000)
#df.Gross

In [313]:
# look for values which have alphabetic characters in them => not in USD and  has to be converted
df[df.Gross.str.contains(pat = "[a-zA-Z]")]

Name  num_ratings  avg_rating  \
IMDB_ID                                                             
2082197                           Barfi!        68152         8.1   
2377938                  Special Chabbis        44672         8.0   
6522546                           Spyder         7799         6.8   
1512888                 Ayirathil Oruvan         2724         7.7   
6148156                     Vikram Vedha        17906         8.7   
2309600                         Singam 2         4966         6.3   
5867800                            Aruvi         8034         8.8   
5451690                   American Satan         2474         5.5   
5956100                  Tiger Zinda Hai        18396         6.1   
5460068                  Emo the Musical          795         6.2   
6878378                          Vivegam         9840         5.9   
3638644                       Seto Surya          362         7.0   
5440700                            Theri        11077         7.2   
1965272                       Velayudham         9750         6.4   
1821478                         Kaavalan         4017         6.9   
6485666                           Mersal        21747         8.0   
3563156                           Anjaan         3414         4.9   
6734984              Duvvada Jagannadham         2451         5.5   
3555036                           Legend         1554         6.5   
3802668         Govindudu Andari Vaadele         1607         5.7   
2204243                         Baadshah         3661         6.5   
6027478                           Dhruva         4629         8.0   
5457772                       Sarrainodu         3137         6.4   
5297256                      Pulimurugan         6133         7.0   
1661031                     Brindaavanam         3195         7.2   
6980546                  Bharat Ane Nenu        13039         8.0   
7098658                            Raazi        16995         7.8   
403935                    Action Jackson         2812         3.3   
3417422                         Drishyam        23724         8.8   
2359810                       Raanjhanaa        26543         7.6   
3848892                             Baby        47710         8.0   
2585562                            Pizza         5450         8.1   
2877108                    Soodhu Kavvum         7153         8.4   
3569782                      Jigarthanda         8325         8.4   
1851988                               Ko         4481         7.8   
5098128                 Nannaku Prematho         7937         7.7   
4727512                      Srimanthudu         9548         7.6   
2304655                     Gabbar Singh         5234         7.1   
3142764                      Race Gurram         7531         7.2   
1729637                        Bodyguard        20075         4.6   
1890493                      Oosaravelli         2946         6.6   
1992138                            Force         6290         6.4   
3495026                              Fan        38733         7.1   
2555958                         Arrambam         8017         7.2   
4258292                 Yennai Arindhaal         7193         7.3   
5178278                          Vedalam         5139         6.3   
3320578                           Veeram         6312         6.6   
1891755                          Billa 2         9798         6.3   
1655607                           Singam         4581         6.7   
2362778  Saheb Biwi Aur Gangster Returns         3491         6.8   
2106537       Matru ki Bijlee ka Mandola         5727         5.7   
1375789                           Race 2        13933         5.3   

        motion_picture_rating                   release_date  duration  \
IMDB_ID                                                                  
2082197             Not Rated  14 September 2012 (Singapore)       151   
2377938             Not Rated        8 February 2013 (India)       144   
6522546      

In [317]:
# remove extra whitespaces, commas:
df['Gross'] = df.Gross.apply(lambda x: re.sub("[,\s]", "", x))
df[df.Gross.str.contains(pat = "[a-zA-Z]")]

Name  num_ratings  avg_rating  \
IMDB_ID                                                             
2082197                           Barfi!        68152         8.1   
2377938                  Special Chabbis        44672         8.0   
6522546                           Spyder         7799         6.8   
1512888                 Ayirathil Oruvan         2724         7.7   
6148156                     Vikram Vedha        17906         8.7   
2309600                         Singam 2         4966         6.3   
5867800                            Aruvi         8034         8.8   
5956100                  Tiger Zinda Hai        18396         6.1   
5460068                  Emo the Musical          795         6.2   
6878378                          Vivegam         9840         5.9   
3638644                       Seto Surya          362         7.0   
5440700                            Theri        11077         7.2   
1965272                       Velayudham         9750         6.4   
1821478                         Kaavalan         4017         6.9   
6485666                           Mersal        21747         8.0   
3563156                           Anjaan         3414         4.9   
6734984              Duvvada Jagannadham         2451         5.5   
3555036                           Legend         1554         6.5   
3802668         Govindudu Andari Vaadele         1607         5.7   
2204243                         Baadshah         3661         6.5   
6027478                           Dhruva         4629         8.0   
5457772                       Sarrainodu         3137         6.4   
5297256                      Pulimurugan         6133         7.0   
1661031                     Brindaavanam         3195         7.2   
6980546                  Bharat Ane Nenu        13039         8.0   
7098658                            Raazi        16995         7.8   
403935                    Action Jackson         2812         3.3   
3417422                         Drishyam        23724         8.8   
2359810                       Raanjhanaa        26543         7.6   
3848892                             Baby        47710         8.0   
2585562                            Pizza         5450         8.1   
2877108                    Soodhu Kavvum         7153         8.4   
3569782                      Jigarthanda         8325         8.4   
1851988                               Ko         4481         7.8   
5098128                 Nannaku Prematho         7937         7.7   
4727512                      Srimanthudu         9548         7.6   
2304655                     Gabbar Singh         5234         7.1   
3142764                      Race Gurram         7531         7.2   
1729637                        Bodyguard        20075         4.6   
1890493                      Oosaravelli         2946         6.6   
1992138                            Force         6290         6.4   
3495026                              Fan        38733         7.1   
2555958                         Arrambam         8017         7.2   
4258292                 Yennai Arindhaal         7193         7.3   
5178278                          Vedalam         5139         6.3   
3320578                           Veeram         6312         6.6   
1891755                          Billa 2         9798         6.3   
1655607                           Singam         4581         6.7   
2362778  Saheb Biwi Aur Gangster Returns         3491         6.8   
2106537       Matru ki Bijlee ka Mandola         5727         5.7   
1375789                           Race 2        13933         5.3   

        motion_picture_rating                   release_date  duration  \
IMDB_ID                                                                  
2082197             Not Rated  14 September 2012 (Singapore)       151   
2377938             Not Rated        8 February 2013 (India)       144   
6522546             Not Rated      27 September 2017 (India)       155   
1512888 

In [318]:
# add 7 trailing zeros for these 4:
# 6980546                 INR 206 Bharat Ane Nenu
# 3142764                 INR 130 Race Gurram
# 6734984                INR 157 Duvvada Jagannadham
# 6522546                INR 124 Spyder

gross_truncated = ["INR206", "INR130","INR157","INR124"]

df['Gross'] = df.Gross.apply(lambda x: x + "0000000" if x in gross_truncated else x)

In [319]:
# for American Satan - VND 74 cumulative worldwide gross - change to USD $226,232
# https://www.the-numbers.com/movie/American-Satan#tab=international
df.at[5451690, 'Gross'] = "226232"

In [320]:
from currency_converter import CurrencyConverter

def convert_currency(x):
    if re.search('[a-zA-Z£]', x) == None:
        return float(x)
    
    split_gross = re.split('(\d+)',x)
    
    # GBP
    if(split_gross[0] == "£"):
        return (c.convert(float(split_gross[1]), 'GBP','USD'))
    
    # NPR isn't supported CurrencyConverter - hard code
    if(split_gross[0]  == "NPR"):
        return (float(split_gross[1])*0.0090)
    
    return (c.convert(float(split_gross[1]), split_gross[0],'USD'))


df['Gross'] = df['Gross'].apply(lambda x : convert_currency(x))

In [281]:
df.head(5)

Name  num_ratings  avg_rating  \
IMDB_ID                                                    
433362              Daybreakers       116014         6.5   
1216492               Leap Year        85208         6.5   
1037705         The Book of Eli       268523         6.9   
1038686                  Legion        91364         5.2   
1244659  Extraordinary Measures        15595         6.5   

        motion_picture_rating                  release_date  duration  \
IMDB_ID                                                                 
433362                      R   14 January 2010 (Singapore)        98   
1216492                    PG  12 February 2010 (Singapore)       100   
1037705                     R     18 March 2010 (Singapore)       118   
1038686                     R   21 January 2010 (Singapore)       100   
1244659                    PG         22 January 2010 (USA)       106   

         num_user_ratings  num_critic_ratings        Gross    Country  ...  \
IMDB_ID                                                                ...   
433362              301.0               291.0   51416464.0  Australia  ...   
1216492             219.0               136.0   25918920.0        USA  ...   
1037705             588.0               331.0  157107755.0        USA  ...   
1038686             328.0               227.0   67918658.0        USA  ...   
1244659              67.0               129.0   11854694.0        USA  ...   

        Musical Mystery  News  Romance  Sci-Fi  Short  Sport  Thriller  War  \
IMDB_ID                                                                       
433362        0       0     0        0       1      0      0         1    0   
1216492       0       0     0        1       0      0      0         0    0   
1037705       0       0     0        0       0      0      0         1    0   
1038686       0       0     0        0       0      0      0         0    0   
1244659       0       0     0        0       0      0      0         0    0   

         Western  
IMDB_ID           
433362         0  
1216492        0  
1037705        0  
1038686        0  
1244659        0  

[5 rows x 37 columns]

In [282]:
# check NaN
df['Gross'].isnull().values.any()

False

In [321]:
df['Gross'].describe()

count    3.867000e+03
mean     6.237718e+07
std      1.747515e+08
min      0.000000e+00
25%      8.006500e+04
50%      1.428647e+06
75%      3.477335e+07
max      2.940555e+09
Name: Gross, dtype: float64

## Categorize movies by gross revenue quintile
Split movies into 5 groups by revenue, and add (one-hot?) columns for classification.

In [322]:
print(list(df.columns.values))
print(df.shape)

['Name', 'num_ratings', 'avg_rating', 'motion_picture_rating', 'release_date', 'duration', 'num_user_ratings', 'num_critic_ratings', 'Gross', 'Country', 'Language', 'Production_House', 'Average_popularity_score_per_movie', 'num_languages', 'Action', 'Adventure', 'Animation', 'Biography', 'Comedy', 'Crime', 'Documentary', 'Drama', 'Family', 'Fantasy', 'History', 'Horror', 'Music', 'Musical', 'Mystery', 'News', 'Romance', 'Sci-Fi', 'Short', 'Sport', 'Thriller', 'War', 'Western']
(3867, 37)


In [218]:
df.head(5)

Name  num_ratings  avg_rating  \
IMDB_ID                                                    
433362              Daybreakers       116014         6.5   
1216492               Leap Year        85208         6.5   
1037705         The Book of Eli       268523         6.9   
1038686                  Legion        91364         5.2   
1244659  Extraordinary Measures        15595         6.5   

        motion_picture_rating                  release_date  duration  \
IMDB_ID                                                                 
433362                      R   14 January 2010 (Singapore)        98   
1216492                    PG  12 February 2010 (Singapore)       100   
1037705                     R     18 March 2010 (Singapore)       118   
1038686                     R   21 January 2010 (Singapore)       100   
1244659                    PG         22 January 2010 (USA)       106   

         num_user_ratings  num_critic_ratings        Gross    Country  ...  \
IMDB_ID                                                                ...   
433362              301.0               291.0   51416464.0  Australia  ...   
1216492             219.0               136.0   25918920.0        USA  ...   
1037705             588.0               331.0  157107755.0        USA  ...   
1038686             328.0               227.0   67918658.0        USA  ...   
1244659              67.0               129.0   11854694.0        USA  ...   

        Musical Mystery  News  Romance  Sci-Fi  Short  Sport  Thriller  War  \
IMDB_ID                                                                       
433362        0       0     0        0       1      0      0         1    0   
1216492       0       0     0        1       0      0      0         0    0   
1037705       0       0     0        0       0      0      0         1    0   
1038686       0       0     0        0       0      0      0         0    0   
1244659       0       0     0        0       0      0      0         0    0   

         Western  
IMDB_ID           
433362         0  
1216492        0  
1037705        0  
1038686        0  
1244659        0  

[5 rows x 37 columns]

#### Divide into quintiles based on gross revenue
This divides into 5 balanced classes.
**`TODO`** Divide into 5 based on manually selected range?

In [323]:
ret_value = pd.qcut(df['Gross'], 5, labels=["very low", "low", "medium", "high", "very high"], retbins = True)

#### Check bucket values

In [324]:
df['gross_category'] = ret_value[0]
ret_value[1]
# low ends at 3.782940e+05, medium ends at 5.823487e+06, high ends at 6.337276e+07

array([0.00000000e+00, 4.64560000e+04, 3.78894000e+05, 5.83402240e+06,
       6.34464402e+07, 2.94055455e+09])

In [287]:
df.groupby('gross_category').size()

gross_category
very low     774
low          773
medium       773
high         773
very high    774
dtype: int64

In [288]:
df_sorted = df.sort_values(['Gross','gross_category'])

#### This prints the whole dataframe (all ~3k rows)! 

In [180]:
#df_sorted

Name  num_ratings  \
IMDB_ID                                                                   
1925479                                       Officer Down       4961.0   
4874206                                         (M)uchenik       3764.0   
4372390                                             Detour       4559.0   
1810697                                       Meeting Evil      11192.0   
1682940                                           Playback       4474.0   
4796122                                            Satanic       5188.0   
5038358                   Des nouvelles de la planète Mars        888.0   
2289920                                    Justice Is Mind         96.0   
1384927                               Death of a Superhero       3206.0   
1493157                                       Nature Calls       2095.0   
2275471                                      A Perfect Man       1792.0   
4428762                                         Éperdument       1116.0   
1503777                                            Illégal        824.0   
5143704                                      Green is Gold        824.0   
2193418                                 Hammer of the Gods       7488.0   
1682186                                           Headshot       1602.0   
1559040                                       Angels Crest       1759.0   
1657299                                    The Decoy Bride       9922.0   
762138                                               Syrup      10166.0   
3334212                                   This Isn't Funny        348.0   
1649443                               [REC] 4: Apocalipsis      14120.0   
3324494              La prochaine fois je viserai le coeur       2172.0   
4439102                                      Officer Downe       1576.0   
1830792                                             Romeos       3001.0   
3130776                                 She's Lost Control        712.0   
2385195                            Rhymes for Young Ghouls        966.0   
2385227                                            Sunrise        246.0   
850677                                        Jack & Diane       2521.0   
1612782                                 The Butterfly Room       1776.0   
1541160                                           Flypaper      30197.0   
1522296                                     Snowman's Land        643.0   
1487118                                        Chalet Girl      22173.0   
2363213                                     Gåten Ragnarok       6894.0   
1641841                                         Skin Trade       6860.0   
2123884                             3 Nights in the Desert       1404.0   
1865346                              Detention of the Dead       2396.0   
1436559                            Love, Wedding, Marriage       8623.0   
1656179                                 I Kissed a Vampire        355.0   
2125439                                          Bestiaire        355.0   
1884457                                        The Package       3606.0   
1480658                                              Eddie       1349.0   
2574576                                          Cut Snake       1127.0   
2241750                                              Drown       1166.0   
1853643                                      Why Stop Now?       7018.0   
2924352                                          Hayride 2        614.0   
1747967                                          Cassadaga       3106.0   
1235841                                         Medianeras      12741.0   
1867093                                      The Samaritan       9000.0   
2726552                                   A Kind of Murder       5740.0   
1885300                                      Best Man Down       8774.0   
1886493                                          Catch .44      15898.0   
3240784                                       Sneakerheadz        617.0   
1772

## Basic Classification Model - Logistic Regression

### Join df with YouTube features, Sentiment features


In [341]:
df_cleaned = df.copy()

In [337]:
df_cleaned.head(5)

Name  num_ratings  avg_rating  \
IMDB_ID                                                    
433362              Daybreakers       116014         6.5   
1216492               Leap Year        85208         6.5   
1037705         The Book of Eli       268523         6.9   
1038686                  Legion        91364         5.2   
1244659  Extraordinary Measures        15595         6.5   

        motion_picture_rating                  release_date  duration  \
IMDB_ID                                                                 
433362                      R   14 January 2010 (Singapore)        98   
1216492                    PG  12 February 2010 (Singapore)       100   
1037705                     R     18 March 2010 (Singapore)       118   
1038686                     R   21 January 2010 (Singapore)       100   
1244659                    PG         22 January 2010 (USA)       106   

         num_user_ratings  num_critic_ratings        Gross    Country  ...  \
IMDB_ID                                                                ...   
433362              301.0               291.0   51416464.0  Australia  ...   
1216492             219.0               136.0   25918920.0        USA  ...   
1037705             588.0               331.0  157107755.0        USA  ...   
1038686             328.0               227.0   67918658.0        USA  ...   
1244659              67.0               129.0   11854694.0        USA  ...   

        Mystery News  Romance  Sci-Fi  Short  Sport  Thriller  War  Western  \
IMDB_ID                                                                       
433362        0    0        0       1      0      0         1    0        0   
1216492       0    0        1       0      0      0         0    0        0   
1037705       0    0        0       0      0      0         1    0        0   
1038686       0    0        0       0      0      0         0    0        0   
1244659       0    0        0       0      0      0         0    0        0   

         gross_category  
IMDB_ID                  
433362             high  
1216492            high  
1037705       very high  
1038686       very high  
1244659            high  

[5 rows x 38 columns]

In [ ]:
# read from YouTube excel file here and join the 2 dataframes for columns - viewCount,  likeCount, dislikeCount, commentCount

In [ ]:
# read from sentiment features

### Dealing with categorical features
Inspect non-numeric columns:

* Country                                 object -- 61 unique - categorize as top 5 vs. others **`TODO`**: Check
* Language                                object -- 77 unique - categorize as top 5 vs. others **`TODO`**: Check
* Production_House                        object -- ~2000+ unique - categorize as top 5 vs. others **`TODO`**: Check
* motion_picture_rating                   object -- only 5 groups 
* Name                                    object -- drop, too unique, unless using to derive a text-based feature
* release_date                            object -- drop, can be used to extract weekend/not later 

In [344]:
df_cleaned.dtypes

Name                                    object
num_ratings                              int64
avg_rating                             float64
motion_picture_rating                   object
release_date                            object
duration                                 int64
num_user_ratings                       float64
num_critic_ratings                     float64
Gross                                  float64
Country                                 object
Language                                object
Production_House                        object
Average_popularity_score_per_movie     float64
num_languages                            int64
Action                                   int64
Adventure                                int64
Animation                                int64
Biography                                int64
Comedy                                   int64
Crime                                    int64
Documentary                              int64
Drama        

#### Check production house split

In [345]:
df_cleaned['Production_House'].dtypes

dtype('O')

In [346]:
df_cleaned['Production_House'].head(5)

IMDB_ID
433362                Lionsgate
1216492      Universal Pictures
1037705     Alcon Entertainment
1038686             Screen Gems
1244659               CBS Films
Name: Production_House, dtype: object

In [364]:
# could do top 5 vs others
df_cleaned.groupby('Production_House').size().sort_values(ascending = False).head(20)

Production_House
 Universal Pictures               80
 Columbia Pictures Corporation    70
 Paramount Pictures               63
 Warner Bros.                     61
 Twentieth Century Fox            51
 Summit Entertainment             35
 Walt Disney Pictures             34
 New Line Cinema                  28
 Lionsgate                        28
 Fox 2000 Pictures                24
 Focus Features                   21
 Fox Searchlight Pictures         21
 Screen Gems                      21
 BBC Films                        19
 Relativity Media                 18
 DreamWorks                       16
 EuropaCorp                       16
 The Weinstein Company            16
 Alcon Entertainment              16
 Millennium Films                 15
dtype: int64

In [367]:
top_production = list(df_cleaned.groupby('Production_House').size().sort_values(ascending = False).head(5).index)

df_cleaned['Production_House'] = df_cleaned.Production_House.apply(lambda x: x if x in top_production
                                         else "Other")

In [368]:
df_cleaned.groupby('Production_House').size().sort_values(ascending = False)

Production_House
Other_Production                  3593
 Universal Pictures                 80
 Columbia Pictures Corporation      70
 Paramount Pictures                 63
 Warner Bros.                       61
dtype: int64

#### Check language split

In [374]:
df_cleaned.groupby('Language').size().sort_values(ascending = False).head(20) # could do English, French, Hindi, Spanish, Mandarin vs. others

Language
English           2931
Other_Language     449
French             194
Hindi              151
Spanish             78
Mandarin            64
dtype: int64

In [372]:
top_language = list(df_cleaned.groupby('Language').size().sort_values(ascending = False).head(5).index)

df_cleaned['Language'] = df_cleaned.Language.apply(lambda x: x if x in top_language
                                         else "Other")

In [373]:
df_cleaned.groupby('Language').size().sort_values(ascending = False)

Language
English           2931
Other_Language     449
French             194
Hindi              151
Spanish             78
Mandarin            64
dtype: int64

#### Check country split

In [375]:
df_cleaned.groupby('Country').size().sort_values(ascending = False).head(20) # could do USA, UK, France, India, Canada, China vs. others

Country
USA            2189
UK              348
France          237
India           198
Canada           97
China            77
Japan            64
South Korea      63
Germany          62
Australia        46
Spain            43
Italy            33
Mexico           30
Ireland          26
Israel           25
Denmark          24
Hong Kong        21
Belgium          21
Norway           17
Sweden           16
dtype: int64

In [378]:
top_countries = list(df_cleaned.groupby('Country').size().sort_values(ascending = False).head(5).index)

df_cleaned['Country'] = df_cleaned.Country.apply(lambda x: x if x in top_countries
                                         else "Other")

In [379]:
df_cleaned.groupby('Country').size().sort_values(ascending = False)

Country
USA              2189
Other_Country     798
UK                348
France            237
India             198
Canada             97
dtype: int64

### One-Hot Encoding 
For categorical features, and the gross_category label.

In [396]:
X = df_cleaned.drop(['gross_category', 'Gross', 'release_date', 'Name'], axis=1) 
# drop is NOT in-place by default, doesn't affect original DF

y = df_cleaned['gross_category'].copy()

In [397]:
X.dtypes

num_ratings                             int64
avg_rating                            float64
motion_picture_rating                  object
duration                                int64
num_user_ratings                      float64
num_critic_ratings                    float64
Country                                object
Language                               object
Production_House                       object
Average_popularity_score_per_movie    float64
num_languages                           int64
Action                                  int64
Adventure                               int64
Animation                               int64
Biography                               int64
Comedy                                  int64
Crime                                   int64
Documentary                             int64
Drama                                   int64
Family                                  int64
Fantasy                                 int64
History                           

In [398]:
#categorical_cols = ["motion_picture_rating", "Country", "Language",  "Production_House"]
X_dummies = pd.get_dummies(X)

In [399]:
X_dummies.shape

(3867, 54)

In [401]:
X_dummies.head(5)

num_ratings  avg_rating  duration  num_user_ratings  \
IMDB_ID                                                        
433362        116014         6.5        98             301.0   
1216492        85208         6.5       100             219.0   
1037705       268523         6.9       118             588.0   
1038686        91364         5.2       100             328.0   
1244659        15595         6.5       106              67.0   

         num_critic_ratings  Average_popularity_score_per_movie  \
IMDB_ID                                                           
433362                291.0                            8.318333   
1216492               136.0                            6.195667   
1037705               331.0                            8.769667   
1038686               227.0                            4.450000   
1244659               129.0                            6.396333   

         num_languages  Action  Adventure  Animation  ...  Language_French  \
IMDB_ID                                               ...                    
433362               1       1          0          0  ...                0   
1216492              2       0          0          0  ...                0   
1037705              1       1          1          0  ...                0   
1038686              1       1          0          0  ...                0   
1244659              1       0          0          0  ...                0   

         Language_Hindi  Language_Mandarin  Language_Other_Language  \
IMDB_ID                                                               
433362                0                  0                        0   
1216492               0                  0                        0   
1037705               0                  0                        0   
1038686               0                  0                        0   
1244659               0                  0                        0   

         Language_Spanish  Production_House_ Columbia Pictures Corporation  \
IMDB_ID                                                                      
433362                  0                                                0   
1216492                 0                                                0   
1037705                 0                                                0   
1038686                 0                                                0   
1244659                 0                                                0   

         Production_House_ Paramount Pictures  \
IMDB_ID                                         
433362                                      0   
1216492                                     0   
1037705                                     0   
1038686                                     0   
1244659                                     0   

         Production_House_ Universal Pictures  Production_House_ Warner Bros.  \
IMDB_ID                                                                         
433362                                      0                               0   
1216492                                     1                               0   
1037705                                     0                               0   
1038686                                     0                               0   
1244659                                     0                               0   

         Production_House_Other_Production  
IMDB_ID                                     
433362                                   1  
1216492                                  0  
1037705                                  1  
1038686                                  1  
1244659                                  1  

[5 rows x 54 columns]

In [404]:
le = preprocessing.LabelEncoder()
le.fit(y)

LabelEncoder()

In [405]:
list(le.classes_)

['high', 'low', 'medium', 'very high', 'very low']

In [406]:
y_encoded = le.transform(y) 

### Split data - train, test

In [407]:
X_train, X_test, y_train, y_test = train_test_split(X_dummies, y_encoded, random_state=1)

In [418]:
lr = LogisticRegression(multi_class = "multinomial", solver = 'lbfgs')
lr.fit(X_train, y_train)

/Users/spatika/anaconda3/envs/BT5153/lib/python3.7/site-packages/sklearn/linear_model/logistic.py:758: ConvergenceWarning: lbfgs failed to converge. Increase the number of iterations.
  "of iterations.", ConvergenceWarning)


LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='multinomial',
          n_jobs=None, penalty='l2', random_state=None, solver='lbfgs',
          tol=0.0001, verbose=0, warm_start=False)

In [419]:
print("Train accuracy: ", lr.score(X_train, y_train))
print("Test accuracy: ", lr.score(X_test, y_test))

Train accuracy:  0.44517241379310346
Test accuracy:  0.46949327817993797


### TODO modelling
1. Choose other candidate models - neural networks, for example like SNAP paper
2. Hyperparameter tuning (gridsearch CV/randomized search CV), pipelining (?)
3. Ensembling models